In [6]:
import os
import mediapipe as mp
import cv2 as cv
import pandas as pd
import numpy as np
from python_speech_features import mfcc
from tsfresh.feature_extraction import extract_features
import torch
from transformers import BertTokenizer, BertModel
import soundfile as sf
import torch.nn.functional as F
from transformers import (
    Wav2Vec2FeatureExtractor,
    Wav2Vec2ForPreTraining,
    Wav2Vec2Model,
)
from transformers.models.wav2vec2.modeling_wav2vec2 import _compute_mask_indices

In [4]:
root = os.path.dirname(os.getcwd())
print("root direction", root)
dataset = os.listdir(root + '/muldataset')
print(dataset)

root direction f:\Project\AMH
['00002-0101', '00002-0102', '00002-0103', '00002-0104', '00002-0105', '00002-0106', '00002-0107', '00002-0108', '00002-0109', '00002-0110', '00002-0111', '00002-0112', '00002-0113', '00002-0114', '00002-0115', '00002-0116', '00002-0117', '00002-0118', '00002-0119', '00002-0120', '00002-0121', '00002-0122', '00002-0123', '00002-0124', '00002-0125', '00002-0126', '00002-0127', '00002-0128', '00002-0129', '00002-0130', '00002-0131', '00002-0132', '00002-0133', '00002-0134', '00002-0135', '00002-0136', '00002-0139', '00002-0140', '00002-0201', '00002-0202', '00002-0204', '00002-0205', '00002-0206', '00002-0207', '00002-0208', '00002-0209', '00002-0210', '00002-0211', '00002-0212', '00002-0213', '00002-0214', '00002-0215', '00002-0216', '00002-0217', '00002-0219', '00002-0221', '00002-0223', '00002-0224', '00002-0225', '00002-0226', '00002-0227', '00002-0229', '00002-0230', '00002-0231', '00002-0233', '00002-0234', '00002-0235', '00002-0236', '00002-0237', '00

In [7]:

def get_landmarks(img_path):
    x = []
    y = []
    z = []

    mp_drawing = mp.solutions.drawing_utils
    mp_drawing_styles = mp.solutions.drawing_styles
    mp_face_mesh = mp.solutions.face_mesh

    with mp_face_mesh.FaceMesh(
            static_image_mode=True,
            max_num_faces=1,
            refine_landmarks=True,
            min_detection_confidence=0.5) as face_mesh:

        image = cv.imread(img_path)
        results = face_mesh.process(cv.cvtColor(image, cv.COLOR_BGR2RGB))

        if not results.multi_face_landmarks:
            print("No landmarks")
            return 0, 0, 0

        for i in range(468):
            x.append(results.multi_face_landmarks[0].landmark[i].x)
            y.append(results.multi_face_landmarks[0].landmark[i].y)
            z.append(results.multi_face_landmarks[0].landmark[i].z)
        # print(x, y, z)

        # output face with 468 landmarks
        annotated_image = image.copy()
        for face_landmarks in results.multi_face_landmarks:
            # print('face_landmarks:', face_landmarks)
            mp_drawing.draw_landmarks(
                image=annotated_image,
                landmark_list=face_landmarks,
                connections=mp_face_mesh.FACEMESH_TESSELATION,
                landmark_drawing_spec=None,
                connection_drawing_spec=mp_drawing_styles
                    .get_default_face_mesh_tesselation_style())
            mp_drawing.draw_landmarks(
                image=annotated_image,
                landmark_list=face_landmarks,
                connections=mp_face_mesh.FACEMESH_CONTOURS,
                landmark_drawing_spec=None,
                connection_drawing_spec=mp_drawing_styles
                    .get_default_face_mesh_contours_style())
            mp_drawing.draw_landmarks(
                image=annotated_image,
                landmark_list=face_landmarks,
                connections=mp_face_mesh.FACEMESH_IRISES,
                landmark_drawing_spec=None,
                connection_drawing_spec=mp_drawing_styles
                    .get_default_face_mesh_iris_connections_style())
        # cv.imwrite('/tmp/annotated_image' + str(idx) + '.png', annotated_image)
        # cv.imshow("Image", annotated_image)
        # cv.waitKey(0)
        # cv.destroyWindow()

        # x = np.array(x).reshape(468, 1)
        # y = np.array(y).reshape(468, 1)
        # z = np.array(z).reshape(468, 1)

        return x,y,z

def judge_face(img_path):
    judge = 1
    mp_face_detection = mp.solutions.face_detection
    mp_drawing = mp.solutions.drawing_utils
    # 0代表近景人脸，1代表远景
    with mp_face_detection.FaceDetection(
            model_selection=0, min_detection_confidence=0.5) as face_detection:

        image = cv.imread(img_path)
        # Convert the BGR image to RGB and process it with MediaPipe Face Detection.
        results = face_detection.process(cv.cvtColor(image, cv.COLOR_BGR2RGB))
        if not results.detections:
            judge = 0
        # print(results.detections)
    return judge

def get_iris(img_path):
    mp_face_detection = mp.solutions.face_detection
    mp_drawing = mp.solutions.drawing_utils
    # 0代表近景人脸，1代表远景
    with mp_face_detection.FaceDetection(
            model_selection=0, min_detection_confidence=0.5) as face_detection:

        image = cv.imread(img_path)
        # Convert the BGR image to RGB and process it with MediaPipe Face Detection.
        results = face_detection.process(cv.cvtColor(image, cv.COLOR_BGR2RGB))
        if not results.detections:
            print("No iris found")
            return 0, 0, 0, 0


        for index, detection in enumerate(results.detections):
            # print(index, detection)
            # print(detection.location_data.relative_bounding_box)
            left_x = detection.location_data.relative_keypoints[0].x
            left_y = detection.location_data.relative_keypoints[0].y
            right_x = detection.location_data.relative_keypoints[1].x
            right_y = detection.location_data.relative_keypoints[1].y
            # print(detection.location_data.relative_keypoints[0].x, detection.location_data.relative_keypoints[0])

        # print(left_x, left_y, right_x, right_y)
        mp_drawing.draw_detection(image, detection)

        annotated_image = image.copy()
        for detection in results.detections:
            # print('Nose tip:')
            # print(mp_face_detection.get_key_point(
            #     detection, mp_face_detection.FaceKeyPoint.NOSE_TIP))
            mp_drawing.draw_detection(annotated_image, detection)
        bboxC = detection.location_data.relative_bounding_box
        ih, iw, ic = image.shape
        bbox = (int(bboxC.xmin * iw), int(bboxC.ymin * ih),
                int(bboxC.width * iw), int(bboxC.height * ih))
        # print(bboxC)
        cv.rectangle(image, bbox, (255, 0, 0), 5)  # 自定义绘制函数，不适用官方的mpDraw.draw_detection
        # cv.imshow('image', image)

        cv.waitKey(0)

    return left_x, left_y, right_x, right_y

def get_index(csv_path):
    df = pd.read_csv(csv_path, usecols=[0,1,2,4,6,7])

    df_br = df['br']
    df_deltabp = df['deltaBp']
    df_hr = df['hr']
    df_hrv = df['hrv']
    df_relax = df['relax']
    df_stress = df['stress']
    br = df_br.tolist()
    deltabp = df_deltabp.tolist()
    hr = df_hr.tolist()
    hrv = df_hrv.tolist()
    relax = df_relax.tolist()
    stress = df_stress.tolist()
    # print(len(br))
    df.insert(df.shape[1], 'id', 1)
    df.insert(df.shape[1], 'time', np.arange(len(br)))

    # print(df)
    ft = extract_features(df, column_id="id", column_sort="time")
    np.nan_to_num(ft)
    # print(np.array(ft).reshape(-1, 2))

    return ft
    
def pert_get_feature(text_list, list_len):
    # Download pretrained model from Internet to "\.cache\torch\transformers\"
    tokenizer = BertTokenizer.from_pretrained('hfl/chinese-pert-large')
    bert = BertModel.from_pretrained('hfl/chinese-pert-large')

    # text_list = ["中文", "自然语言处理"]
    inputs = tokenizer(text_list, return_tensors="pt", padding=True)  # "pt"表示"pytorch"
    outputs = bert(**inputs)

    # print(outputs)
    # print(outputs.pooler_output)
    # print(outputs.pooler_output.shape)
    text_ft = outputs.pooler_output.detach().numpy().reshape(list_len, -1)
    print(text_ft.shape)
    return text_ft

def roberta_get_feature(text_list, list_len):
    # Download pretrained model from Internet to "\.cache\torch\transformers\"
    tokenizer = BertTokenizer.from_pretrained('hfl/chinese-roberta-wwm-ext-large')
    bert = BertModel.from_pretrained('hfl/chinese-roberta-wwm-ext-large')

    # text_list = ["中文", "自然语言处理"]
    inputs = tokenizer(text_list, return_tensors="pt", padding=True)  # "pt"表示"pytorch"
    outputs = bert(**inputs)

    # print(outputs)
    # print(outputs.pooler_output)
    # print(outputs.pooler_output.shape)
    text_ft = outputs.pooler_output.detach().numpy().reshape(list_len, -1)
    print(text_ft.shape)
    return text_ft

def macberta_get_feature(text_list, list_len):
    # Download pretrained model from Internet to "\.cache\torch\transformers\"
    tokenizer = BertTokenizer.from_pretrained('hfl/chinese-macbert-large')
    bert = BertModel.from_pretrained('hfl/chinese-macbert-large')

    # text_list = ["中文", "自然语言处理"]
    inputs = tokenizer(text_list, return_tensors="pt", padding=True)  # "pt"表示"pytorch"
    outputs = bert(**inputs)

    # print(outputs)
    # print(outputs.pooler_output)
    # print(outputs.pooler_output.shape)
    text_ft = outputs.pooler_output.detach().numpy().reshape(list_len, -1)
    print(text_ft.shape)
    return text_ft

def get_answer_text(csv_path):
    
        
    df = pd.read_csv(csv_path, encoding='GB18030')
    text_list = df['answer'].tolist()
    # print(text_list

    return  text_list

def get_average_feature(text_list):
    return np.mean(text_list, axis=0)

def get_audio_embeddings(audio_path, model_id="facebook/wav2vec2-base-960h"):
        model_path = "./"
        wav_path=audio_path
        mask_prob=0.0
        mask_length=10

        feature_extractor = Wav2Vec2FeatureExtractor.from_pretrained(model_path)
        # model = Wav2Vec2Model.from_pretrained(model_path)
        model = Wav2Vec2ForPreTraining.from_pretrained(model_path)

        device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        model = model.to(device)
        model = model.half()
        model.eval()

        y, sample_rate = sf.read(audio_path)
        input_values = feature_extractor(y, return_tensors="pt").input_values
        input_values = input_values.half()
        input_values = input_values.to(device)

        batch_size, raw_sequence_length = input_values.shape
        sequence_length = model._get_feat_extract_output_lengths(raw_sequence_length)
        mask_time_indices = _compute_mask_indices((batch_size, sequence_length), mask_prob=0.0, mask_length=2)
        mask_time_indices = torch.tensor(mask_time_indices, device=input_values.device, dtype=torch.long)

        with torch.no_grad():
            outputs = model(input_values, mask_time_indices=mask_time_indices, output_hidden_states=True)
            last_hidden_state = outputs.hidden_states[-1]
            embed = last_hidden_state.detach().cpu().numpy().reshape(-1, 1024)
            embed = np.mean(embed,axis=0)
            # print(embed.shape)
        # processor = Wav2Vec2Processor.from_pretrained(model_id)
        # model = Wav2Vec2Model.from_pretrained(model_id)
        
        # length = len(y)
        # # print(sample_rate)
        # if length > 160000:
        #     y = y[:160000]
        # elif length <= 160000:
        #     y = np.concatenate((y, np.zeros(160000-length)))
        # mfcc_feat = mfcc(y, sample_rate, nfilt=40, numcep=13, nfft=2048)
        # mfcc_feat = mfcc_feat.reshape(1, -1)
        # print(mfcc_feat.shape)
        # with torch.no_grad():
            
        #     input_values = processor(y, sampling_rate=sample_rate, return_tensors="pt", padding=True).input_values
        #     hidden_states = model(input_values).last_hidden_state
        #     embed = hidden_states.detach().numpy().reshape(1, -1)
        return embed
        


In [56]:
audio_embeddings = get_audio_embeddings('./wKgIb2Ch5kmAOm61AAKFAAab0GQ224.wav')

# print(mfcc_fe.shape)
print(audio_embeddings.shape)


You are using a model of type hubert to instantiate a model of type wav2vec2. This is not supported for all configurations of models and can yield errors.
Some weights of Wav2Vec2ForPreTraining were not initialized from the model checkpoint at ./ and are newly initialized: ['project_hid.weight', 'quantizer.codevectors', 'project_q.bias', 'project_q.weight', 'project_hid.bias', 'quantizer.weight_proj.weight', 'quantizer.weight_proj.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.


(1024,)
(1024,)


In [9]:
from sklearn import preprocessing

if __name__ == '__main__':
    # totalnum = []
    face_x = []
    face_y = []
    face_z = []

    leftx = []
    lefty = []
    rightx = []
    righty = []
    scaler = preprocessing.StandardScaler()
    root = os.path.dirname(os.getcwd())
    print("root direction", root)
    dataset = os.listdir(root + '/muldataset')
    del dataset[-1]
    # print(dataset)

    for sample in dataset:
        if 'label' in sample:
            continue
        sample_path = root + '/muldataset' + '/' + sample #样本文件夹
        print(sample_path)
        sample_file = os.listdir(sample_path) #样本文件夹内文件列表
        if 'face_landmarks.csv' in sample_file:
            continue
        video_judge = 0 #判断文件夹内是否有视频
        # print(sample_file)
        
        '''
Test how many image of folder      ==694 
        num = 0
        for detail in sample_file:
            if '2021' in detail and '.png' in detail:
                num += 1
        totalnum.append(num)
        print("{sample} have {num} face image".format(sample=sample, num=num))    
        
    print(max(totalnum)) 
transfer video to images      
        for detail in sample_file:
            # print(sample_path)
            
            if '.mp4' in detail:
                timeF = 30
                video_path = sample_path + '/' + detail
                print(video_path)
                vode = cv.VideoCapture(video_path)

                success,frame = vode.read()
                i = 0
                j = 0

                while success:
                    i += 1
                    if i % timeF==0:
                        j += 1
                        cv.imwrite(sample_path + '/videoimg2021_' + str(j) + '.jpg', frame)
                    success,frame = vode.read()
                print('Finish!')
                
                
            elif 'videoimg_2021' in detail:
                 os.remove(sample_path + '/' + detail)
            
            else:
                continue
        '''
        
        for detail in sample_file:    
            if '.mp4' in detail:
                video_judge = 1
            if video_judge == 1 and 'videoimg2021' in detail:
                # 判断是否有人脸
                judge = judge_face(sample_path + '/' + detail)
                # 有人脸则获取人脸区域的468个标记点
                if judge == 1:
                    x, y, z = get_landmarks(sample_path + '/' + detail)
                    # 如果没有返回468个标记点
                    if x == 0:
                        continue
                    face_x.append(x)
                    face_y.append(y)
                    face_z.append(z)

                    left_eye_x, left_eye_y, right_eye_x, right_eye_y = get_iris(sample_path + '/' + detail)
                    leftx.append(left_eye_x)
                    lefty.append(left_eye_y)
                    rightx.append(right_eye_x)
                    righty.append(right_eye_y)
                    # print(np.array(face_landmarks).shape)
                    # print(face_landmarks.shape)
            
            if video_judge == 0 and '2021' in detail and '.png' in detail:
                # 判断是否有人脸
                judge = judge_face(sample_path + '/' + detail)
                # 有人脸则获取人脸区域的468个标记点
                if judge == 1:
                    x, y, z = get_landmarks(sample_path + '/' + detail)
                    # 如果没有返回468个标记点
                    if x == 0:
                        continue
                    face_x.append(x)
                    face_y.append(y)
                    face_z.append(z)

                    left_eye_x, left_eye_y, right_eye_x, right_eye_y = get_iris(sample_path + '/' + detail)
                    leftx.append(left_eye_x)
                    lefty.append(left_eye_y)
                    rightx.append(right_eye_x)
                    righty.append(right_eye_y)
                    # print(np.array(face_landmarks).shape)
                    # print(face_landmarks.shape)
            else:
                continue
        
        face_x = np.array(face_x).reshape(-1, 1)
        face_y = np.array(face_y).reshape(-1, 1)
        face_z = np.array(face_z).reshape(-1, 1)
        
        # print(np.array(face_x).shape)
        # face_landmarks = np.array(face_landmarks).reshape(-1,3)
        face_landmarks = np.stack((face_x, face_y, face_z), axis=1)
        face_landmarks = face_landmarks.reshape(-1, 3)
        # face_landmarks = scaler.fit_transform(face_landmarks)
        print(np.array(face_landmarks).shape)

        # 写入csv
        name = ['x', 'y', 'z']
        landmarks = pd.DataFrame(columns=name, data=face_landmarks)
        # print(landmarks)
        # print(face_x)
        landmarks.to_csv(sample_path + '/face_landmarks.csv', encoding='gbk')

        #清空landmarks列表
        face_landmarks = []
        face_x = []
        face_y = []
        face_z = []

        for i in range(0, 694 - len(leftx)):
            leftx.append(np.mean(leftx))
            lefty.append(np.mean(lefty))
            rightx.append(np.mean(rightx))
            righty.append(np.mean(righty))

        leftx = np.array(leftx).reshape(-1, 1)
        lefty = np.array(lefty).reshape(-1, 1)
        rightx = np.array(rightx).reshape(-1, 1)
        righty = np.array(righty).reshape(-1, 1)

        eye_landmarks = np.stack((leftx, lefty, rightx, righty), axis=1)
        eye_landmarks = eye_landmarks.reshape(-1, 4)
        # eye_landmarks = scaler.fit_transform(eye_landmarks)
        print(np.array(eye_landmarks).shape)

        # 写入csv
        name = ['left_x', 'left_y', 'right_x', 'right_y']
        landmarks = pd.DataFrame(columns=name, data=eye_landmarks)
        # print(landmarks)
        # print(face_x)
        landmarks.to_csv(sample_path + '/iris_location.csv', encoding='gbk')

        # 情况landmarks列表
        eye_landmarks = []
        leftx = []
        lefty = []
        rightx = []
        righty = []


root direction f:\Project\AMH
f:\Project\AMH/muldataset/00002-0101
f:\Project\AMH/muldataset/00002-0102
f:\Project\AMH/muldataset/00002-0103
f:\Project\AMH/muldataset/00002-0104
f:\Project\AMH/muldataset/00002-0105
f:\Project\AMH/muldataset/00002-0106
f:\Project\AMH/muldataset/00002-0107
f:\Project\AMH/muldataset/00002-0108
f:\Project\AMH/muldataset/00002-0109
f:\Project\AMH/muldataset/00002-0110
f:\Project\AMH/muldataset/00002-0111
f:\Project\AMH/muldataset/00002-0112
f:\Project\AMH/muldataset/00002-0113
f:\Project\AMH/muldataset/00002-0114
f:\Project\AMH/muldataset/00002-0115
f:\Project\AMH/muldataset/00002-0116
f:\Project\AMH/muldataset/00002-0117
f:\Project\AMH/muldataset/00002-0118
f:\Project\AMH/muldataset/00002-0119
f:\Project\AMH/muldataset/00002-0120
f:\Project\AMH/muldataset/00002-0121
f:\Project\AMH/muldataset/00002-0122
f:\Project\AMH/muldataset/00002-0123
f:\Project\AMH/muldataset/00002-0124
f:\Project\AMH/muldataset/00002-0125
f:\Project\AMH/muldataset/00002-0126
f:\Proje

In [10]:
root = os.path.dirname(os.getcwd())
print("root direction", root)

dataset = os.listdir(root + '/muldataset')
# print(dataset_class)
index_ft = []
name = ['TSfresh']
for sample in dataset:
    if 'label' in sample:
        continue
    sample_path = root + '/muldataset' + '/' + sample
    print(sample_path)
    sample_file = os.listdir(sample_path)
    # print(sample_file)
    
    if 'Physical_feature.csv' in sample_file:
        continue
    for detail in sample_file:
        if 'emotion.csv' in detail:
            detail_path = sample_path + '/' + detail
            print(detail_path)
            index_ft.append(get_index(detail_path))
            print(np.array(index_ft).shape)

            
            index_ft = np.array(index_ft).reshape(-1, 1)
            index_ft[np.isnan(index_ft)] = 0
            print(np.any(np.isnan(index_ft)))
                # 写入csv   
            landmarks = pd.DataFrame(columns=name, data=index_ft)
                # print(landmarks)
                # print(face_x)
            landmarks.to_csv(sample_path + '/Physical_feature.csv', encoding='gbk')
            index_ft = []
            break

root direction f:\Project\AMH
f:\Project\AMH/muldataset/00002-0101
f:\Project\AMH/muldataset/00002-0102
f:\Project\AMH/muldataset/00002-0103
f:\Project\AMH/muldataset/00002-0104
f:\Project\AMH/muldataset/00002-0105
f:\Project\AMH/muldataset/00002-0106
f:\Project\AMH/muldataset/00002-0107
f:\Project\AMH/muldataset/00002-0108
f:\Project\AMH/muldataset/00002-0109
f:\Project\AMH/muldataset/00002-0110
f:\Project\AMH/muldataset/00002-0111
f:\Project\AMH/muldataset/00002-0112
f:\Project\AMH/muldataset/00002-0113
f:\Project\AMH/muldataset/00002-0114
f:\Project\AMH/muldataset/00002-0115
f:\Project\AMH/muldataset/00002-0116
f:\Project\AMH/muldataset/00002-0117
f:\Project\AMH/muldataset/00002-0118
f:\Project\AMH/muldataset/00002-0119
f:\Project\AMH/muldataset/00002-0120
f:\Project\AMH/muldataset/00002-0121
f:\Project\AMH/muldataset/00002-0122
f:\Project\AMH/muldataset/00002-0123
f:\Project\AMH/muldataset/00002-0124
f:\Project\AMH/muldataset/00002-0125
f:\Project\AMH/muldataset/00002-0126
f:\Proje

In [20]:
root = os.path.dirname(os.getcwd())
print("root direction", root)

dataset = os.listdir(root + '/muldataset')
del dataset[-1]
# print(dataset)

for sample in dataset:
    sample_path = root + '/muldataset' + '/' + sample
        # print(sample_class_path)
    sample_file = os.listdir(sample_path)
    # print(sample_file)
    if 'text_feature.csv' in sample_file:
        print("asa")
    

root direction f:\Project\AMH
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
asa
as

In [17]:
root = os.path.dirname(os.getcwd())
print("root direction", root)

dataset = os.listdir(root + '/muldataset')
del dataset[-1]
# print(dataset)

for sample in dataset:
    sample_path = root + '/muldataset' + '/' + sample
    # print(sample_path)
    sample_file = os.listdir(sample_path)
    
    if(int(sample[7:]) >= 614):
        print(sample_path)
        print(sample[7:])

root direction f:\Project\AMH
f:\Project\AMH/muldataset/00002-0614
614
f:\Project\AMH/muldataset/00002-0615
615
f:\Project\AMH/muldataset/00002-0616
616
f:\Project\AMH/muldataset/00002-0618
618
f:\Project\AMH/muldataset/00002-0619
619
f:\Project\AMH/muldataset/00002-0620
620
f:\Project\AMH/muldataset/00002-0621
621
f:\Project\AMH/muldataset/00002-0623
623
f:\Project\AMH/muldataset/00002-0624
624
f:\Project\AMH/muldataset/00002-0626
626
f:\Project\AMH/muldataset/00002-0627
627
f:\Project\AMH/muldataset/00002-0628
628
f:\Project\AMH/muldataset/00002-0630
630
f:\Project\AMH/muldataset/00002-0631
631
f:\Project\AMH/muldataset/00002-0633
633
f:\Project\AMH/muldataset/00002-0634
634
f:\Project\AMH/muldataset/00002-0701
701
f:\Project\AMH/muldataset/00002-0702
702
f:\Project\AMH/muldataset/00002-0703
703
f:\Project\AMH/muldataset/00002-0704
704
f:\Project\AMH/muldataset/00002-0705
705
f:\Project\AMH/muldataset/00002-0706
706
f:\Project\AMH/muldataset/00002-0707
707
f:\Project\AMH/muldataset/0

In [49]:
def get_wav2vec(csv_path):
    df = pd.read_csv(csv_path, usecols=[1])
    df_wav2vec = df['wav2vec'].values.tolist()
    
    return df_wav2vec

root = os.path.dirname(os.getcwd())
print("root direction", root)

dataset = os.listdir(root + '/muldataset')
del dataset[-1]
# print(dataset)

for sample in dataset:
    if 'label' in sample:
        continue
    sample_path = root + '/muldataset' + '/' + sample
    # print(sample_path)
    sample_file = os.listdir(sample_path)
    # print(sample_file)
    
    for detail in sample_file:
        if 'wav2vec' in detail:
                    # print(sample_path + '/' + detail)
                    temp_wav2vec = get_wav2vec(sample_path + '/' + detail)
                    # print(len(temp_wav2vec))
                    if len(temp_wav2vec) == 1024:
                        break
                    else:
                        print(sample_path + '/' + detail)

root direction f:\Project\AMH
f:\Project\AMH/muldataset/00004-0135/wav2vec.csv
f:\Project\AMH/muldataset/00004-0242/wav2vec.csv
f:\Project\AMH/muldataset/00004-0247/wav2vec.csv
f:\Project\AMH/muldataset/00004-0311/wav2vec.csv
f:\Project\AMH/muldataset/00004-0319/wav2vec.csv
f:\Project\AMH/muldataset/00004-0407/wav2vec.csv
f:\Project\AMH/muldataset/00004-0419/wav2vec.csv
f:\Project\AMH/muldataset/00004-0427/wav2vec.csv
f:\Project\AMH/muldataset/00004-0431/wav2vec.csv
f:\Project\AMH/muldataset/00004-0435/wav2vec.csv
f:\Project\AMH/muldataset/00004-0518/wav2vec.csv
f:\Project\AMH/muldataset/00004-0526/wav2vec.csv
f:\Project\AMH/muldataset/00004-0529/wav2vec.csv
f:\Project\AMH/muldataset/00004-0712/wav2vec.csv
f:\Project\AMH/muldataset/00004-0727/wav2vec.csv
f:\Project\AMH/muldataset/00004-0733/wav2vec.csv
f:\Project\AMH/muldataset/00004-0734/wav2vec.csv
f:\Project\AMH/muldataset/00004-0818/wav2vec.csv
f:\Project\AMH/muldataset/00004-0832/wav2vec.csv
f:\Project\AMH/muldataset/00004-0904/wa

In [17]:
pert = []
roberta = []
macberta = []
name = ['pert', 'roberta', 'macberta']

root = os.path.dirname(os.getcwd())
print("root direction", root)

dataset = os.listdir(root + '/muldataset')
del dataset[-1]
# print(dataset)

for sample in dataset:
    if 'label' in sample:
        continue
    sample_path = root + '/muldataset' + '/' + sample
    print(sample_path)
    sample_file = os.listdir(sample_path)
    # print(sample_file)
    if 'con_text_feature.csv' in sample_file:
        continue
    for detail in sample_file:
        
        if 'answer.csv' in detail:
            #提取答案到text_list
            detail_path = sample_path + '/' + detail
            text_list = get_answer_text(detail_path)
            if len(text_list) == 0:
                break
            print(text_list)
            text_seq = text_list[0]
            for i in range(1, len(text_list)):
                text_seq = text_list[i] + text_seq
            text_seq = [text_seq]
            print(text_seq)

            pert_ft = pert_get_feature(text_list, len(text_list))
            pert.append(get_average_feature(pert_ft))
            print(np.array(pert).shape)
            # print(get_average_feature(pert_ft))

            roberta_ft = roberta_get_feature(text_list, len(text_list))
            roberta.append(get_average_feature(roberta_ft))
            # print(np.array(roberta).shape)
            # print(get_average_feature(roberta_ft))

            macberta_ft = macberta_get_feature(text_list, len(text_list))
            macberta.append(get_average_feature(macberta_ft))
            # print(np.array(macberta).shape)
            # print(get_average_feature(macberta_ft))

            pert = np.array(pert).reshape(-1, 1)
            roberta = np.array(roberta).reshape(-1, 1)
            macberta = np.array(macberta).reshape(-1, 1)

            text_sum = np.stack((pert, roberta, macberta), axis=1)
            text_sum = text_sum.reshape(-1, 3)

                # 写入csv
            landmarks = pd.DataFrame(columns=name, data=text_sum)
                # print(landmarks)
                # print(face_x)
            landmarks.to_csv(sample_path + '/text_feature.csv', encoding='gbk')

            text_sum = []
            pert = []
            roberta = []
            macberta = []

            pert_ft = pert_get_feature(text_seq, len(text_seq))
            pert.append(get_average_feature(pert_ft))
            print(np.array(pert).shape)
            # print(get_average_feature(pert_ft))

            roberta_ft = roberta_get_feature(text_seq, len(text_seq))
            roberta.append(get_average_feature(roberta_ft))
            # print(np.array(roberta).shape)
            # print(get_average_feature(roberta_ft))

            macberta_ft = macberta_get_feature(text_seq, len(text_seq))
            macberta.append(get_average_feature(macberta_ft))
            # print(np.array(macberta).shape)
            # print(get_average_feature(macberta_ft))

            pert = np.array(pert).reshape(-1, 1)
            roberta = np.array(roberta).reshape(-1, 1)
            macberta = np.array(macberta).reshape(-1, 1)

            text_sum = np.stack((pert, roberta, macberta), axis=1)
            text_sum = text_sum.reshape(-1, 3)

                # 写入csv
            landmarks = pd.DataFrame(columns=name, data=text_sum)
                # print(landmarks)
                # print(face_x)
            landmarks.to_csv(sample_path + '/con_text_feature.csv', encoding='gbk')

            text_sum = []
            pert = []
            roberta = []
            macberta = []



root direction f:\Project\AMH
f:\Project\AMH/muldataset/00002-0101
f:\Project\AMH/muldataset/00002-0102
f:\Project\AMH/muldataset/00002-0103
f:\Project\AMH/muldataset/00002-0104
f:\Project\AMH/muldataset/00002-0105
f:\Project\AMH/muldataset/00002-0106
f:\Project\AMH/muldataset/00002-0107
f:\Project\AMH/muldataset/00002-0108
f:\Project\AMH/muldataset/00002-0109
f:\Project\AMH/muldataset/00002-0110
f:\Project\AMH/muldataset/00002-0111
f:\Project\AMH/muldataset/00002-0112
f:\Project\AMH/muldataset/00002-0113
f:\Project\AMH/muldataset/00002-0114
f:\Project\AMH/muldataset/00002-0115
f:\Project\AMH/muldataset/00002-0116
f:\Project\AMH/muldataset/00002-0117
f:\Project\AMH/muldataset/00002-0118
f:\Project\AMH/muldataset/00002-0119
f:\Project\AMH/muldataset/00002-0120
f:\Project\AMH/muldataset/00002-0121
f:\Project\AMH/muldataset/00002-0122
f:\Project\AMH/muldataset/00002-0123
f:\Project\AMH/muldataset/00002-0124
f:\Project\AMH/muldataset/00002-0125
f:\Project\AMH/muldataset/00002-0126
f:\Proje

In [24]:
root = os.path.dirname(os.getcwd())
print("root direction", root)

dataset = os.listdir(root + '/muldataset')
del dataset[-1]
# print(dataset)

for sample in dataset:
    sample_path = root + '/muldataset' + '/' + sample
    
    sample_file = os.listdir(sample_path)
    # print(sample_file)
    if 'Physical_feature.csv' in sample_file:
        continue
    else:
        print(sample_path)

 

root direction f:\Project\AMH


In [5]:
if __name__ == '__main__':
    root = os.path.dirname(os.getcwd())
    print("root direction", root)
    dataset = os.listdir(root + '/muldataset')
    for sample in dataset:
        sample_path = root + '/muldataset' + '/' + sample #样本文件夹
        # print(sample_path)
        sample_file = os.listdir(sample_path) #样本文件夹内文件列表
        # print(sample_file)
        for detail in sample_file:
            sample_path = root + '/muldataset' + '/' + sample
            if 'face_landmarks' in detail:
                df = pd.read_csv(sample_path + '/' + detail, usecols=[1,2,3])
                face_x = df['x'].values.tolist()
                num = np.array(face_x).shape[0] / 468
                if num <= 12:
                    print(sample_path)


root direction f:\Project\AMH
f:\Project\AMH/muldataset/00002-1212
f:\Project\AMH/muldataset/00004-0138
f:\Project\AMH/muldataset/00004-0231
f:\Project\AMH/muldataset/00004-0240
f:\Project\AMH/muldataset/00004-0256
f:\Project\AMH/muldataset/00004-0334
f:\Project\AMH/muldataset/00004-0349
f:\Project\AMH/muldataset/00004-0708
f:\Project\AMH/muldataset/00004-0816
f:\Project\AMH/muldataset/00004-0828
f:\Project\AMH/muldataset/00004-0937
f:\Project\AMH/muldataset/00004-1219
f:\Project\AMH/muldataset/00004-1642
f:\Project\AMH/muldataset/00004-1917
f:\Project\AMH/muldataset/00004-1937
f:\Project\AMH/muldataset/00004-2325


NotADirectoryError: [WinError 267] 目录名称无效。: 'f:\\Project\\AMH/muldataset/label.csv'

In [25]:
root = os.path.dirname(os.getcwd())
print("root direction", root)
dataset = os.listdir(root + '/muldataset')
del dataset[-1]

label_path = root + '/muldataset/label.csv'
df = pd.read_csv(label_path)
# print(dataset)
folder_name = df['folder'].values.tolist()
folder_index = []
drop_index = []
print(folder_name.index('00004-0104'))

for sample in dataset:
    if sample in folder_name:
        folder_index.append(folder_name.index(sample))
    else:
        print(sample)
print(np.array(folder_index).shape)

diff = list(set(folder_name) ^ set(dataset))
print(np.array(diff).shape)
for i in diff:
    drop_index.append(folder_name.index(i))
print(drop_index)
drop_index = sorted(drop_index, reverse=True)
print(drop_index)

for i in drop_index:
    df.drop(df.index[i],  inplace=True)
df.to_csv(root + '/muldataset/labels.csv', index=False, encoding="gbk")


root direction f:\Project\AMH
416
(1101,)
(7,)
[227, 111, 351, 317, 218, 65, 370]
[370, 351, 317, 227, 218, 111, 65]


In [28]:
root = os.path.dirname(os.getcwd())
print("root direction", root)
dataset = os.listdir(root + '/muldataset')
del dataset[-1]

label_path = root + '/muldataset/label.csv'
df = pd.read_csv(label_path)
folder_name = df['folder'].values.tolist()
print(len(folder_name))

diff = list(set(folder_name) ^ set(dataset))
print(diff)

root direction f:\Project\AMH
1101
[]


In [5]:
def get_audio_embeddings(audio_path, model_id="facebook/wav2vec2-base-960h"):
        model_path = "./"
        wav_path=audio_path
        mask_prob=0.0
        mask_length=10

        feature_extractor = Wav2Vec2FeatureExtractor.from_pretrained(model_path)
        # model = Wav2Vec2Model.from_pretrained(model_path)
        model = Wav2Vec2ForPreTraining.from_pretrained(model_path)

        device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        model = model.to(device)
        model = model.half()
        model.eval()

        y, sample_rate = sf.read(audio_path)
        input_values = feature_extractor(y, return_tensors="pt").input_values
        input_values = input_values.half()
        input_values = input_values.to(device)

        batch_size, raw_sequence_length = input_values.shape
        sequence_length = model._get_feat_extract_output_lengths(raw_sequence_length)
        mask_time_indices = _compute_mask_indices((batch_size, sequence_length), mask_prob=0.0, mask_length=2)
        mask_time_indices = torch.tensor(mask_time_indices, device=input_values.device, dtype=torch.long)

        with torch.no_grad():
            outputs = model(input_values, mask_time_indices=mask_time_indices, output_hidden_states=True)
            last_hidden_state = outputs.hidden_states[-1]
            embed = last_hidden_state.detach().cpu().numpy().reshape(-1, 1024)
            embed = np.mean(embed,axis=0)
        return embed

hubert = []
MFCC = []

root = os.path.dirname(os.getcwd())
print("root direction", root)
dataset = os.listdir(root + '/muldataset')
# print(dataset)
del dataset[-1]

for sample in dataset:
    if 'label' in sample:
        continue
    temp_MFCC = []
    temp_wav2vec = []
    judge = 0
    sample_path = root + '/muldataset' + '/' + sample
    # print(sample_path)
    sample_file = os.listdir(sample_path)

    for detail in sample_file:  
        if '.wav' in detail:
            detail_path = sample_path + '/' + detail
            print(detail_path)
            embed = get_audio_embeddings(detail_path)
            temp_wav2vec.append(embed)
            # temp_wav2vec.append(audio_embeddings)
            # print(np.array(MFCC).shape)

    # avg_MFCC = np.mean(temp_MFCC, axis=0)
    avg_wav2vec = np.mean(temp_wav2vec, axis=0)
    # MFCC.append(avg_MFCC)
    hubert.append(avg_wav2vec)
    # print(np.array(MFCC).shape)
    print(np.array(hubert).shape)

    # MFCC = np.array(MFCC).reshape(-1, 1)
    hubert = np.array(hubert).reshape(-1, 1)
            
    # 写入csv\
    name = ['wav2vec']
    landmarks = pd.DataFrame(columns=name, data=hubert)
        # print(landmarks)
        # print(face_x)
    landmarks.to_csv(sample_path + '/wav2vec.csv', encoding='gbk')
    
    hubert = []



You are using a model of type hubert to instantiate a model of type wav2vec2. This is not supported for all configurations of models and can yield errors.


root direction f:\Project\AMH
f:\Project\AMH/muldataset/00002-0101/wKgIb2CiGLSAWWhkAAQ9AHdR2yQ370.wav


Some weights of Wav2Vec2ForPreTraining were not initialized from the model checkpoint at ./ and are newly initialized: ['project_hid.bias', 'project_q.bias', 'project_q.weight', 'quantizer.weight_proj.weight', 'quantizer.codevectors', 'quantizer.weight_proj.bias', 'project_hid.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.
You are using a model of type hubert to instantiate a model of type wav2vec2. This is not supported for all configurations of models and can yield errors.


f:\Project\AMH/muldataset/00002-0101/wKgIb2CiGMaASyAkAAXhAFmuv0Q219.wav


Some weights of Wav2Vec2ForPreTraining were not initialized from the model checkpoint at ./ and are newly initialized: ['project_hid.bias', 'project_q.bias', 'project_q.weight', 'quantizer.weight_proj.weight', 'quantizer.codevectors', 'quantizer.weight_proj.bias', 'project_hid.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.
You are using a model of type hubert to instantiate a model of type wav2vec2. This is not supported for all configurations of models and can yield errors.


...

f:\Project\AMH/muldataset/00004-2448/wKgIb2FyM5WASfyMAAJxANwflcE635.wav


Some weights of Wav2Vec2ForPreTraining were not initialized from the model checkpoint at ./ and are newly initialized: ['project_hid.bias', 'project_q.bias', 'project_q.weight', 'quantizer.weight_proj.weight', 'quantizer.codevectors', 'quantizer.weight_proj.bias', 'project_hid.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.
You are using a model of type hubert to instantiate a model of type wav2vec2. This is not supported for all configurations of models and can yield errors.


f:\Project\AMH/muldataset/00004-2448/wKgIb2FyM6mAcABFAAN_AKXYdxs273.wav


Some weights of Wav2Vec2ForPreTraining were not initialized from the model checkpoint at ./ and are newly initialized: ['project_hid.bias', 'project_q.bias', 'project_q.weight', 'quantizer.weight_proj.weight', 'quantizer.codevectors', 'quantizer.weight_proj.bias', 'project_hid.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.


(1, 1024)


In [29]:
from python_speech_features import mfcc

def get_audio_embeddings(audio_path, model_id="facebook/wav2vec2-base-960h"):
        y, sample_rate = sf.read(audio_path)

        length = len(y)
        # print(sample_rate)
        if length > 160000:
            y = y[:160000]
        elif length <= 160000:
            y = np.concatenate((y, np.zeros(160000-length)))
        mfcc_feat = mfcc(y, sample_rate, nfilt=40, numcep=13, nfft=2048)
        mfcc_feat = mfcc_feat.reshape(1, -1)
        print(mfcc_feat.shape)
      
        return mfcc_feat

hubert = []
mfcc_ft = []

root = os.path.dirname(os.getcwd())
print("root direction", root)
dataset = os.listdir(root + '/muldataset')
# print(dataset)
del dataset[-1]

for sample in dataset:
    if 'label' in sample:
        continue
    temp_MFCC = []
    temp_wav2vec = []
    judge = 0
    sample_path = root + '/muldataset' + '/' + sample
    print(sample_path)
    sample_file = os.listdir(sample_path)
    # print(sample_file)
    # if 'mfcc.csv' in sample_file:
    #     continue
    for detail in sample_file:  
        if '.wav' in detail:
            detail_path = sample_path + '/' + detail
            print(detail_path)
            embed = get_audio_embeddings(detail_path)
            # temp_wav2vec.append(embed)
            temp_MFCC.append(embed)
            # temp_wav2vec.append(audio_embeddings)
            # print(np.array(MFCC).shape)
        else:
            continue

    avg_MFCC = np.mean(temp_MFCC, axis=0)
    # avg_wav2vec = np.mean(temp_wav2vec, axis=0)
    mfcc_ft.append(avg_MFCC)
    # hubert.append(avg_wav2vec)
    print(np.array(mfcc_ft).shape)
    # print(np.array(hubert).shape)

    mfcc_ft = np.array(mfcc_ft).reshape(-1, 1)
    # hubert = np.array(hubert).reshape(-1, 1)
            
    # 写入csv\
    name = ['MFCC']
    landmarks = pd.DataFrame(columns=name, data=mfcc_ft)
        # print(landmarks)
        # print(face_x)
    landmarks.to_csv(sample_path + '/mfcc.csv', encoding='gbk')
    
    hubert = []
    mfcc_ft = []



root direction f:\Project\AMH
f:\Project\AMH/muldataset/00002-0101
f:\Project\AMH/muldataset/00002-0101/wKgIb2CiGLSAWWhkAAQ9AHdR2yQ370.wav
(1, 12987)
f:\Project\AMH/muldataset/00002-0101/wKgIb2CiGMaASyAkAAXhAFmuv0Q219.wav
(1, 12987)
f:\Project\AMH/muldataset/00002-0101/wKgIb2CiGNuAHMDkAAdnANG2ozo203.wav
(1, 12987)
f:\Project\AMH/muldataset/00002-0101/wKgIb2CiGO-AfoNsAAJYAK6PxY8561.wav
(1, 12987)
f:\Project\AMH/muldataset/00002-0101/wKgIb2CiGOSAVmDWAAJYAB1O9vs846.wav
(1, 12987)
(1, 1, 12987)
f:\Project\AMH/muldataset/00002-0102
f:\Project\AMH/muldataset/00002-0102/wKgIb2CiGS2ABeQyAAOEAD_Zo30909.wav
(1, 12987)
f:\Project\AMH/muldataset/00002-0102/wKgIb2CiGSGAY-nGAASXAB1LQtc429.wav
(1, 12987)
f:\Project\AMH/muldataset/00002-0102/wKgIb2CiGTeAFueUAAM-AP-mtdo324.wav
(1, 12987)
f:\Project\AMH/muldataset/00002-0102/wKgIb2CiGU6AJ48aAAOnAGolEeY481.wav
(1, 12987)
f:\Project\AMH/muldataset/00002-0102/wKgIb2CiGUGAYm8kAAK8AMhNmY0903.wav
(1, 12987)
(1, 1, 12987)
f:\Project\AMH/muldataset/00002-0103
f

In [7]:
root = os.path.dirname(os.getcwd())
print("root direction", root)
label_path = root + '/muldataset/label.csv'
df = pd.read_csv(label_path, usecols=[1,2,3,4,5,6,7,8,9,10,11,12])
# print(df)
dep = df['depression'].values.tolist()
inter = df['interpersonal tension'].values.tolist()
anx = df['anxiety'].values.tolist()
obs = df['obsessive-compulsive'].values.tolist()
par = df['paranoia'].values.tolist()
hos = df['hostility'].values.tolist()
aca = df['academic stress'].values.tolist()
mal = df['maladjustment'].values.tolist()
emo = df['emotional imbalance'].values.tolist()
psy = df['psychological imbalance'].values.tolist()
sui = df['suicidal tendency'].values.tolist()
overall = df['overall condition'].values.tolist()

print("Depression number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=dep.count(1), healthy=dep.count(0)))
print("Interpersonal tension number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=inter.count(1), healthy=inter.count(0)))
print("Anxiety number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=anx.count(1), healthy=anx.count(0)))
print("Obsessive-compulsive number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=obs.count(1), healthy=obs.count(0)))
print("Paranoia number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=par.count(1), healthy=par.count(0)))
print("Hostility number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=hos.count(1), healthy=hos.count(0)))
print("Academic stress number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=aca.count(1), healthy=aca.count(0)))
print("Maladjustment number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=mal.count(1), healthy=mal.count(0)))
print("Emotional imbalance number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=emo.count(1), healthy=emo.count(0)))
print("Psychological imbalance number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=psy.count(1), healthy=psy.count(0)))
print("Suicidal tendency number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=sui.count(1), healthy=sui.count(0)))
print("Overall conditions number:{unhealthy}, and healthy number:{healthy} ".format(unhealthy=overall.count(1), healthy=overall.count(0)))

root direction f:\Project\AMH
Depression number:350, and healthy number:674 
Interpersonal tension number:279, and healthy number:745 
Anxiety number:390, and healthy number:634 
Obsessive-compulsive number:447, and healthy number:577 
Paranoia number:240, and healthy number:784 
Hostility number:258, and healthy number:766 
Academic stress number:452, and healthy number:572 
Maladjustment number:184, and healthy number:840 
Emotional imbalance number:394, and healthy number:630 
Psychological imbalance number:155, and healthy number:869 
Suicidal tendency number:255, and healthy number:769 
Overall conditions number:273, and healthy number:751 
